In [1]:
!pip install pyspark==3.5.5

In [1]:
# %load_ext autoreload
# %autoreload 2
# %reload_ext autoreload

import os
ROOT_DIR = '/workspace/NN'
os.chdir(ROOT_DIR)

import shutil
import kagglehub
import torch
from pyspark.sql import SparkSession
import socket

dataset_path = os.path.join(ROOT_DIR, 'neural', 'datasets', 'spark', 'test_1')
weight_path = os.path.join(ROOT_DIR, 'neural', 'weights', 'lab_5', 'kmeans')
os.makedirs(dataset_path, exist_ok=True)
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')



print(socket.gethostbyname("spark-master"))
driver_host = socket.gethostbyname(socket.gethostname())
print(driver_host)
driver_host = socket.gethostbyname("spark-master")
print(driver_host)
driver_host = "producer"
os.environ["PYSPARK_SUBMIT_ARGS"] = f"""
--master spark://spark-master:7077
--conf spark.driver.host={driver_host}
--conf spark.driver.port=45555
--conf spark.executor.memory=1G
--conf spark.executor.cores=1
pyspark-shell
"""
os.environ["JAVA_HOME"] = "/usr/lib/jvm/java-11-openjdk-amd64"
# os.environ['PYSPARK_PYTHON'] = '/usr/bin/python3'  # путь к Python в контейнере
# os.environ['SPARK_HOME'] = '/opt/spark'            # путь к Spark, укажи реальный
# os.environ['PYSPARK_DRIVER_PYTHON'] = 'jupyter'

MONGO_USER = os.environ["MONGO_USER"]
MONGO_PASS = os.environ["MONGO_PASSWORD"]
MONGO_ADDR = f"{MONGO_USER}:{MONGO_PASS}@mongodb:27017"  # :27017

def spark_app_generator(name):
    spark = SparkSession.builder \
        .master("spark://spark-master:7077") \
        .appName(name) \
         .config("spark.driver.bindAddress", "0.0.0.0") \
        .config("spark.executor.memory", "1g") \
        .config("spark.driver.memory", "1g") \
    .config("spark.jars.packages", "org.mongodb.spark:mongo-spark-connector_2.12:10.3.0,com.redislabs:spark-redis_2.12:3.1.0") \
    .config("spark.mongodb.read.connection.uri", f"mongodb://{MONGO_ADDR}") \
    .config("spark.mongodb.write.connection.uri", f"mongodb://{MONGO_ADDR}") \
    .config("spark.redis.host", "redis") \
    .config("spark.redis.port", "6379") \
    .config("spark.redis.db", "0") \
        .getOrCreate()

        # .config("spark.hadoop.hadoop.home.dir", "/hadoop/dfs/name") \
    # .config("spark.hadoop.fs.defaultFS", "hdfs://namenode:9000") \
    # .config("spark.hadoop.dfs.client.use.namenode.hostname", "true") \
    print(spark.sparkContext.getConf().get("spark.jars.packages"))
    return spark  # /openfoodfacts.products


172.22.0.4
172.18.0.2
172.22.0.4


In [2]:
spark = spark_app_generator('test_data_loading_to_redis')
# Предположим, есть DataFrame df
df = spark.createDataFrame([(1, "Alice"), (2, "Bob"), (3, "Bob-5")], ["id", "name"])

df \
 .write\
 .format("org.apache.spark.sql.redis")\
 .option("table", "test_results_py")\
 .option("key.column", "id")\
 .mode("overwrite")\
 .save()
spark.stop()

:: loading settings :: url = jar:file:/usr/local/lib/python3.12/site-packages/pyspark/jars/ivy-2.5.1.jar!/org/apache/ivy/core/settings/ivysettings.xml


Ivy Default Cache set to: /root/.ivy2/cache
The jars for the packages stored in: /root/.ivy2/jars
org.mongodb.spark#mongo-spark-connector_2.12 added as a dependency
com.redislabs#spark-redis_2.12 added as a dependency
:: resolving dependencies :: org.apache.spark#spark-submit-parent-9c0b1bba-0872-45e4-81b4-9714854dfecf;1.0
	confs: [default]
	found org.mongodb.spark#mongo-spark-connector_2.12;10.3.0 in central
	found org.mongodb#mongodb-driver-sync;4.8.2 in central
	[4.8.2] org.mongodb#mongodb-driver-sync;[4.8.1,4.8.99)
	found org.mongodb#bson;4.8.2 in central
	found org.mongodb#mongodb-driver-core;4.8.2 in central
	found org.mongodb#bson-record-codec;4.8.2 in central
	found com.redislabs#spark-redis_2.12;3.1.0 in central
	found redis.clients#jedis;3.9.0 in central
	found org.slf4j#slf4j-api;1.7.30 in central
	found org.apache.commons#commons-pool2;2.11.1 in central
downloading https://repo1.maven.org/maven2/org/mongodb/spark/mongo-spark-connector_2.12/10.3.0/mongo-spark-connector_2.12-

org.mongodb.spark:mongo-spark-connector_2.12:10.3.0,com.redislabs:spark-redis_2.12:3.1.0


In [14]:
# spark = spark_app_generator('test_data_loading_to_redis')

df = spark.read \
    .format("org.apache.spark.sql.redis") \
    .option("table", "test_results_py_2") \
    .load()

df.show()
# spark.stop()

25/04/25 13:42:14 WARN TaskSetManager: Lost task 0.0 in stage 77.0 (TID 59018) (172.22.0.5 executor 2): org.apache.spark.SparkRuntimeException: Error while encoding: java.lang.RuntimeException: java.lang.String is not a valid external type for schema of vector
if (assertnotnull(input[0, org.apache.spark.sql.Row, true]).isNullAt) null else staticinvoke(class org.apache.spark.unsafe.types.UTF8String, StringType, fromString, validateexternaltype(getexternalrowfield(assertnotnull(input[0, org.apache.spark.sql.Row, true]), 0, _id), StringType, ObjectType(class java.lang.String)), true, false, true) AS _id#1555
if (assertnotnull(input[0, org.apache.spark.sql.Row, true]).isNullAt) null else staticinvoke(class org.apache.spark.unsafe.types.UTF8String, StringType, fromString, validateexternaltype(getexternalrowfield(assertnotnull(input[0, org.apache.spark.sql.Row, true]), 1, product_name), StringType, ObjectType(class java.lang.String)), true, false, true) AS product_name#1556
if (assertnotnull

Py4JJavaError: An error occurred while calling o615.showString.
: org.apache.spark.SparkException: Job aborted due to stage failure: Task 0 in stage 77.0 failed 4 times, most recent failure: Lost task 0.3 in stage 77.0 (TID 59021) (172.22.0.5 executor 2): org.apache.spark.SparkRuntimeException: Error while encoding: java.lang.RuntimeException: java.lang.String is not a valid external type for schema of vector
if (assertnotnull(input[0, org.apache.spark.sql.Row, true]).isNullAt) null else staticinvoke(class org.apache.spark.unsafe.types.UTF8String, StringType, fromString, validateexternaltype(getexternalrowfield(assertnotnull(input[0, org.apache.spark.sql.Row, true]), 0, _id), StringType, ObjectType(class java.lang.String)), true, false, true) AS _id#1555
if (assertnotnull(input[0, org.apache.spark.sql.Row, true]).isNullAt) null else staticinvoke(class org.apache.spark.unsafe.types.UTF8String, StringType, fromString, validateexternaltype(getexternalrowfield(assertnotnull(input[0, org.ap

In [13]:
import redis

client = redis.Redis(
    host='redis',
    port=6379,
    db=0,
    decode_responses=True  # получаем str вместо bytes
)
keys = client.keys('test_results_py:*')
for key in keys:
    print(key, client.hgetall(key))

test_results_py:3850334343901 {'ingredients_n': '16', 'scans_n': '6', 'product_name': 'Crunchy muesli s voćem', 'features': '[1.0861376704175882,0.0,0.28542419390778684,0.0]', 'additives_n': '0', 'ingredients_sweeteners_n': '0', 'prediction': '1'}
test_results_py:0015100001659 {'scans_n': '2', 'ingredients_n': '10', 'product_name': 'Fettuccine', 'prediction': '1', 'additives_n': '0', 'features': '[0.6788360440109926,0.0,0.09514139796926227,0.0]', 'ingredients_sweeteners_n': '0'}
test_results_py:4388844015913 {'prediction': '1', 'product_name': 'Creme au caramel', 'features': '[0.6788360440109926,0.0,0.047570698984631135,0.0]', 'additives_n': '0', 'scans_n': '1', 'ingredients_sweeteners_n': '0', 'ingredients_n': '10'}
test_results_py:4061461511340 {'features': '[1.289788483620886,0.0,0.33299489289241796,0.412968127534788]', 'product_name': 'Streichzarte Leberwurst', 'scans_n': '7', 'ingredients_sweeteners_n': '0', 'prediction': '2', 'ingredients_n': '19', 'additives_n': '1'}
test_result

KeyboardInterrupt: 

In [2]:
from pyspark.sql.types import (StructType, StructField,
                               StringType, IntegerType, MapType,
                               DoubleType
                               )

# Пример определения схемы. Настройте схему под структуру ваших данных.
custom_schema = StructType([
    StructField("_id", StringType(), True),
    StructField("product_name", StringType(), True),
    # Если nutriments представляет собой динамические поля, лучше сохранить его как MapType.
    StructField("nutriments", MapType(StringType(), StringType()), True),
    # Если есть другие поля, укажите их типы.
    StructField("quantity", StringType(), True),
     StructField("ingredients_sweeteners_n", IntegerType(), True),
     StructField("ingredients_percent_analysis", IntegerType(), True),
     StructField("ingredients_non_nutritive_sweeteners_n", IntegerType(), True),
     StructField("ingredients_n", IntegerType(), True),
    StructField("ingredients_from_palm_oil_n", IntegerType(), True),
    StructField("ingredients_from_or_that_may_be_from_palm_oil_n", IntegerType(), True),
    StructField("additives_n", IntegerType(), True),
    StructField("unique_scans_n", IntegerType(), True),
    StructField("scans_n", IntegerType(), True),
    StructField("rev", IntegerType(), True),
    StructField("popularity_key", IntegerType(), True),
    StructField("packagings_n", IntegerType(), True),
    StructField("packagings_complete", IntegerType(), True),
    StructField("nutrition_score_warning_no_fiber", IntegerType(), True),
    StructField("nutrition_score_warning_fruits_vegetables_nuts_estimate", IntegerType(), True),
    StructField("nutrition_score_beverage", IntegerType(), True),
    StructField("nutriscore_score_opposite", IntegerType(), True),
    StructField("nutriscore_score", IntegerType(), True),
    StructField("environmental_score_score", IntegerType(), True),
    StructField("completeness", DoubleType(), True),
    StructField("complete", IntegerType(), True),

    StructField("energy_100g", IntegerType(), True),
    StructField("proteins_100g", IntegerType(), True),
    StructField("carbohydrates_100g", IntegerType(), True),
    StructField("fat_100g", IntegerType(), True),
    StructField("sugars_100g", IntegerType(), True),
    StructField("saturated-fat_100g", IntegerType(), True),
    StructField("salt_100g", IntegerType(), True),
    StructField("sodium_100g", IntegerType(), True),


])

spark = spark_app_generator('lab_6')
df = spark.read.schema(custom_schema).format("mongodb") \
  .options(host="mongo:27017", database="off", collection='products').load()  # , database="off", collection='products'

# Просмотр схемы и первых строк
print(df.count())
df.printSchema()
df.show(20)


:: loading settings :: url = jar:file:/usr/local/lib/python3.12/site-packages/pyspark/jars/ivy-2.5.1.jar!/org/apache/ivy/core/settings/ivysettings.xml


Ivy Default Cache set to: /root/.ivy2/cache
The jars for the packages stored in: /root/.ivy2/jars
org.mongodb.spark#mongo-spark-connector_2.12 added as a dependency
com.redislabs#spark-redis_2.12 added as a dependency
:: resolving dependencies :: org.apache.spark#spark-submit-parent-ffbc9e00-e313-409b-8990-bb770b90b3d7;1.0
	confs: [default]
	found org.mongodb.spark#mongo-spark-connector_2.12;10.3.0 in central
	found org.mongodb#mongodb-driver-sync;4.8.2 in central
	[4.8.2] org.mongodb#mongodb-driver-sync;[4.8.1,4.8.99)
	found org.mongodb#bson;4.8.2 in central
	found org.mongodb#mongodb-driver-core;4.8.2 in central
	found org.mongodb#bson-record-codec;4.8.2 in central
	found com.redislabs#spark-redis_2.12;3.1.0 in central
	found redis.clients#jedis;3.9.0 in central
	found org.slf4j#slf4j-api;1.7.30 in central
	found org.apache.commons#commons-pool2;2.11.1 in central
downloading https://repo1.maven.org/maven2/org/mongodb/spark/mongo-spark-connector_2.12/10.3.0/mongo-spark-connector_2.12-

org.mongodb.spark:mongo-spark-connector_2.12:10.3.0,com.redislabs:spark-redis_2.12:3.1.0


3791250
root
 |-- _id: string (nullable = true)
 |-- product_name: string (nullable = true)
 |-- nutriments: map (nullable = true)
 |    |-- key: string
 |    |-- value: string (valueContainsNull = true)
 |-- quantity: string (nullable = true)
 |-- ingredients_sweeteners_n: integer (nullable = true)
 |-- ingredients_percent_analysis: integer (nullable = true)
 |-- ingredients_non_nutritive_sweeteners_n: integer (nullable = true)
 |-- ingredients_n: integer (nullable = true)
 |-- ingredients_from_palm_oil_n: integer (nullable = true)
 |-- ingredients_from_or_that_may_be_from_palm_oil_n: integer (nullable = true)
 |-- additives_n: integer (nullable = true)
 |-- unique_scans_n: integer (nullable = true)
 |-- scans_n: integer (nullable = true)
 |-- rev: integer (nullable = true)
 |-- popularity_key: integer (nullable = true)
 |-- packagings_n: integer (nullable = true)
 |-- packagings_complete: integer (nullable = true)
 |-- nutrition_score_warning_no_fiber: integer (nullable = true)
 |-- 

25/04/24 15:29:18 WARN SparkStringUtils: Truncated the string representation of a plan since it was too large. This behavior can be adjusted by setting 'spark.sql.debug.maxToStringFields'.


+------------+--------------------+--------------------+------------------+------------------------+----------------------------+--------------------------------------+-------------+---------------------------+-----------------------------------------------+-----------+--------------+-------+---+--------------+------------+-------------------+--------------------------------+-------------------------------------------------------+------------------------+-------------------------+----------------+-------------------------+------------------+--------+-----------+-------------+------------------+--------+-----------+------------------+---------+-----------+
|         _id|        product_name|          nutriments|          quantity|ingredients_sweeteners_n|ingredients_percent_analysis|ingredients_non_nutritive_sweeteners_n|ingredients_n|ingredients_from_palm_oil_n|ingredients_from_or_that_may_be_from_palm_oil_n|additives_n|unique_scans_n|scans_n|rev|popularity_key|packagings_n|packagings_

3791250

In [9]:
spark.stop()

In [3]:
from pyspark.ml.feature import VectorAssembler, StandardScaler

spark = spark_app_generator('test_mongo_data_analysis')
df = spark.read.schema(custom_schema).format("mongodb") \
  .options(host="mongo:27017", database="off", collection='products').load()

# Выбор числовых признаков
numeric_features = [ '_id', 'product_name',
                      'ingredients_n', 'ingredients_sweeteners_n', 'scans_n', 'additives_n',
# 'energy_100g',
# 'proteins_100g',
# 'carbohydrates_100g',
# 'fat_100g',

# 'sugars_100g',
# 'saturated-fat_100g',
# 'salt_100g',
# 'sodium_100g',
]
# Удаление строк с пропущенными значениями
df_clean = df.select(numeric_features).dropna()
print(df_clean.count())
# df_clean.show(20)


25/04/24 15:29:22 WARN SparkSession: Using an existing Spark session; only runtime SQL configurations will take effect.


org.mongodb.spark:mongo-spark-connector_2.12:10.3.0,com.redislabs:spark-redis_2.12:3.1.0


560304


In [ ]:
print(df_clean.count())

In [5]:
# Сбор признаков в вектор
numeric_features_2 = ['ingredients_n', 'ingredients_sweeteners_n', 'scans_n', 'additives_n',]
assembler = VectorAssembler(inputCols=numeric_features_2, outputCol="features_assembled")
df_vector = assembler.transform(df_clean)

# Масштабирование признаков
scaler = StandardScaler(inputCol="features_assembled", outputCol="features")
scaler_model = scaler.fit(df_vector)
df_scaled = scaler_model.transform(df_vector)

In [6]:
from pyspark.ml.clustering import KMeans
from pyspark.ml.evaluation import ClusteringEvaluator


# df_small = df_scaled.limit(100)
# Обучение модели k-средних
kmeans = KMeans().setK(4).setSeed(1).setFeaturesCol("features")
model = kmeans.fit(df_scaled)



25/04/24 18:25:05 WARN InstanceBuilder: Failed to load implementation from:dev.ludovic.netlib.blas.JNIBLAS


In [7]:
# Предсказание кластеров
predictions = model.transform(df_scaled)
result = predictions.select(
    "_id",
    "product_name",
    'ingredients_n', 'ingredients_sweeteners_n', 'scans_n', 'additives_n',
    "features", "prediction"
)
# result.show()
# Оценка модели
evaluator = ClusteringEvaluator()
silhouette = evaluator.evaluate(predictions)
print(f"Silhouette Score: {silhouette}")

# Центры кластеров
centers = model.clusterCenters()
for idx, center in enumerate(centers):
    print(f"Cluster {idx} center: {center}")

Silhouette Score: 0.4454473796868009
Cluster 0 center: [3.37750473 0.29785837 0.20376838 3.08076544]
Cluster 1 center: [0.46579649 0.01237958 0.29957661 0.14874909]
Cluster 2 center: [1.54019743 0.14427791 0.25957434 1.19594653]
Cluster 3 center: [1.43516994 5.50452079 0.30287615 2.48096947]


# Lab 6

In [8]:
result.show(10)

+------------+--------------------+-------------+------------------------+-------+-----------+--------------------+----------+
|         _id|        product_name|ingredients_n|ingredients_sweeteners_n|scans_n|additives_n|            features|prediction|
+------------+--------------------+-------------+------------------------+-------+-----------+--------------------+----------+
|    00000000|           erytritol|            2|                       0|      1|          1|[0.13576720880219...|         1|
|000000000063|Mozzarella Schnit...|           21|                       0|      1|          0|[1.42555569242308...|         1|
|    00000001|Wild Norwegian El...|            8|                       0|      1|          3|[0.54306883520879...|         2|
|  0000000105|Paleta gran reser...|           14|                       1|      1|          2|[0.95037046161538...|         2|
|    00000002|Filets de poulet ...|            5|                       0|      1|          0|[0.33941802200549

In [12]:

result \
 .write\
 .format("org.apache.spark.sql.redis")\
 .option("table", "test_results_py_2")\
 .option("key.column", "_id")\
 .mode("overwrite")\
 .save()

In [12]:

# weight_path = os.path.join(ROOT_DIR, 'neural', 'weights', 'lab_5', 'kmeans_3')
# os.makedirs(weight_path, exist_ok=True)
# model.save("/opt/bitnami/spark/work/labs/lab_5/kmeans_5")
model.save('/opt/bitnami/spark/work/labs/lab_5/kmeans_7')

In [6]:
# Не забудьте остановить SparkSession по завершении работы
spark.stop()

In [13]:
from pyspark.ml.clustering import KMeansModel

loaded_model = KMeansModel.load("/opt/bitnami/spark/work/labs/lab_5/kmeans_7")


UnsupportedOperationException: empty collection

In [12]:
from pyspark.ml.clustering import KMeans
from pyspark.ml.feature import VectorAssembler
from pyspark.sql import SparkSession

# Инициализация SparkSession
spark = SparkSession.builder \
    .appName("KMeansExample") \
    .getOrCreate()

# Пример данных
data = [
    (0.0, 0.0),
    (1.0, 1.0),
    (9.0, 8.0),
    (8.0, 9.0)
]
columns = ["x", "y"]
df = spark.createDataFrame(data, columns)

# Преобразование признаков в вектор
assembler = VectorAssembler(inputCols=["x", "y"], outputCol="features")
dataset = assembler.transform(df)

# Обучение модели KMeans
kmeans = KMeans().setK(2).setSeed(1)
model = kmeans.fit(dataset)

# Сохранение модели
model.save("/opt/bitnami/spark/work/labs/lab_5/kmeans_test")

# Загрузка модели
from pyspark.ml.clustering import KMeansModel
loaded_model = KMeansModel.load("/opt/bitnami/spark/work/labs/lab_5/kmeans_test")

# Применение загруженной модели
predictions = loaded_model.transform(dataset)
predictions.show()


25/04/22 14:25:04 WARN SparkSession: Using an existing Spark session; only runtime SQL configurations will take effect.


UnsupportedOperationException: empty collection